In [1]:
%load_ext autoreload
%autoreload 2  

import sys
import os
import torch

# Add the parent directory of the parent directory to the path
sys.path.append(os.path.abspath(os.path.join(os.getcwd(), '../..')))

# Now you can import modules from two levels up



In [4]:
'''
from utils.formatting.folder2txt import dataset_to_txt 
dataset_to_txt(
    dataset_path=("../datasets/openwebtext/train"),
    output_txt_path=("../datasets/openwebtext.txt"),
    text_key="text"
)
'''


'\ndataset_to_txt(\n    dataset_path=("../datasets/openwebtext/train"),\n    output_txt_path=("../datasets/openwebtext.txt"),\n    text_key="text"\n)\n'

In [ ]:
from utils.model.token_counter import TokenCounter
'''
token_counter = TokenCounter()
token_counter.fit_counter_txt("datasets/openwebtext.txt", start_line=0, end_line=100_000_000)
token_counter.save("tokenizer/token_counter.json")
token_counter = TokenCounter.load( "tokenizer/token_counter.json")
'''




In [9]:
from utils.model.tokenizer import Tokenizer
''' 
tokenizer = Tokenizer(vocab_size = 50000, max_length = 2048)
tokenizer.update_dicts(token_counter.counter)
tokenizer.save("tokenizer/tokenizer.json")
'''
tokenizer = Tokenizer.load("tokenizer/tokenizer.json")


In [14]:

'''
from utils.formatting.txt2bin import tokenize_to_dataset
tokenize_to_dataset(
    tokenizer=tokenizer,
    input_path=("datasets/openwebtext.txt"),
    train_path=("datasets/openwebtext_train.bin"),
    test_path=("datasets/openwebtext_test.bin"),
    valid_path=("datasets/openwebtext_valid.bin"),
    train_ratio=0.8,
    test_ratio=0.1,
    valid_ratio=0.1,
    start_line=0,
    dtype=torch.int32
)

'''

Counting lines...
Processed 1000/166005717 lines (0.00%)
Line: A Port Authority policeman named Chip Michaels texts Wildstein a report from the streets: “Its fkd up here.” Michaels is another guy from Livingston. He and his brother, a Republican lobbyist, have known both Wildstein and Christie for years. Michaels picks up Wildstein and takes him on a drive to observe the traffic. Then they go to a diner, where they have breakfast and discuss Christie’s presidential hopes.
IDs: [14, 2200, 1505, 12354, 1035, 3623, 17993, 5766, 45979, 14, 342, 72, 40, 1964, 59, 68, 115, 19, 24, 17, 101, 170, 41, 69, 17993, 49, 211, 929, 72, 18965, 41, 65, 45, 78, 1726, 42, 14, 674, 11816, 42, 71, 382, 201, 45979, 45, 5717, 51, 148, 41, 17993, 3697, 101, 45979, 45, 785, 146, 54, 14, 1046, 43, 6364, 40, 1546, 41, 149, 76, 195, 43, 14, 16695, 42, 154, 76, 71, 5116, 45, 2009, 5717, 50, 32, 1117, 2214, 41]
Processed 2000/166005717 lines (0.00%)
Line: ST. LOUIS — Peter Chiarelli knew this was going to happen. T

KeyboardInterrupt: 

In [8]:
from utils.dataset.unstrucuted_text_dataset import TransformerDataset

train_dataset = TransformerDataset(
    path=("../datasets/openwebtext_train.bin"),
    input_len=64,
    
    output_len=32,
    stride=96,
    dtype=torch.int32
)

test_dataset = TransformerDataset(
    path=("../datasets/openwebtext_test.bin"),
    input_len=64,
    output_len=32,
    stride=96,
    dtype=torch.int32)

valid_dataset = TransformerDataset(
    path=("../datasets/openwebtext_valid.bin"),
    input_len=64,
    output_len=32,
    stride=96,
    dtype=torch.int32)

print(f"Train dataset length: {len(train_dataset)}")
print(f"Test dataset length: {len(test_dataset)}")
print(f"Valid dataset length: {len(valid_dataset)}")
print(f"Train dataset sample: {train_dataset[0]}")

Train dataset length: 67779936
Test dataset length: 8455666
Valid dataset length: 8469514
Train dataset sample: (tensor([   0, 2139,   12, 4866,   12, 3194,    6, 9542,   31, 2009,   30,   12,
          12, 5642, 1538,    6,    3,   11, 1604,    9,    3,   37,  196,    6,
        2418, 2271,    9, 8398, 1529,  308,   44,   10,  648, 1200,  728,  387,
         101,   10, 7492,  741,  183,    3,    4,  433,    6,  491,   21,   28,
        1670,   68,  363,    5,    4,  536,  260, 2009,  732,  741, 7100,    3,
           3,   27,    4,  109, 1824], dtype=torch.int32), tensor([   0,   37,    4, 1200,    7,  117,    4, 1317,  158,    4,  387,    5,
        2009, 2129,  526,    6,  266,   23, 3733,   25,   92,    8,    4, 2271,
           6,   14,    4,  288, 1418, 2218,    4, 7492,  104,    1],
       dtype=torch.int32))


c:\Users\silly\Desktop\coding_projects\torchrvn\utils\dataset\unstrucuted_text_dataset.py:35: UserWarning: The given buffer is not writable, and PyTorch does not support non-writable tensors. This means you can write to the underlying (supposedly non-writable) buffer using the tensor. You may want to copy the buffer to protect its data or make it writable before converting it to a tensor. This type of warning will be suppressed for the rest of this program. (Triggered internally at C:\actions-runner\_work\pytorch\pytorch\pytorch\torch\csrc\utils\tensor_new.cpp:1567.)
  tokens = torch.frombuffer(buf, dtype=self.dtype)


In [9]:
from algorithms.transformer.classic_transformer import Transformer
transformer = Transformer(
    vocab_size=tokenizer.vocab_size,
    d_model=512,
    num_heads=8,
    num_encoders=4,
    num_decoders=4,
    d_ff=512)

In [ ]:
from utils.training.train import train_model
from torch import nn

train_model(
    train_dataset=train_dataset,
    test_dataset=test_dataset,
    model=transformer,
    loss_fn=nn.CrossEntropyLoss(),
    optimizer=torch.optim.Adam(transformer.parameters(), lr=0.0001),
    batch_size=128,
    num_epochs=10,
    save_folder_path="../checkpoints"
)



Epoch 1/10
Batch 10, Train Loss: 7.5100
Test Loss: 7.1942
Batch 20, Train Loss: 6.6918
Test Loss: 6.5968
Batch 30, Train Loss: 6.4749
Test Loss: 6.2945
Batch 40, Train Loss: 6.1710
Test Loss: 6.2187
Batch 50, Train Loss: 6.0568
Test Loss: 6.1076
Batch 60, Train Loss: 6.0178
Test Loss: 6.0146
Batch 70, Train Loss: 6.0575
Test Loss: 6.0829
Batch 80, Train Loss: 6.0930
Test Loss: 5.9030
Batch 90, Train Loss: 5.9102
Test Loss: 5.9746
Batch 100, Train Loss: 5.8625
Test Loss: 5.9118
Batch 110, Train Loss: 5.8015
Test Loss: 5.8227
Batch 120, Train Loss: 5.7405
Test Loss: 5.7427
Batch 130, Train Loss: 5.8298
Test Loss: 5.8632
Batch 140, Train Loss: 5.7438
Test Loss: 5.8153
Batch 150, Train Loss: 5.7857
Test Loss: 5.7062
Batch 160, Train Loss: 5.6851
Test Loss: 5.6831
Batch 170, Train Loss: 5.7437
Test Loss: 5.7181
Batch 180, Train Loss: 5.6669
Test Loss: 5.5791
Batch 190, Train Loss: 5.6750
Test Loss: 5.6932
Batch 200, Train Loss: 5.6930
Test Loss: 5.6401
Batch 210, Train Loss: 5.5738
Test Lo